
#  $\lambda$-calcul

## Analyseur lexical

In [1]:
from sly import Lexer

In [56]:
class LambdaSyntaxError(Exception):
    def __init__(self, msg):
        self.message = msg

In [61]:
class Lambda_lexer(Lexer):
    tokens = {VAR, LPAR, RPAR, LAMBDA, POINT}
    VAR = r'[a-zA-Z][a-zA-Z0-9]*'
    LPAR = r'\('
    RPAR = r'\)'
    LAMBDA = r'\!|λ'
    POINT = r'\.'
    ignore = ' \t'
    
    # Define a rule so we can track line numbers
    @_(r'\n+')
    def ignore_newline(self, t):
        self.lineno += len(t.value)
        
    def error(self, t):
        raise LambdaSyntaxError('Caractère illégal : {:s} at position {:d}'.format(t.value[0], t.index))
        self.index += 1

In [62]:
lexer = Lambda_lexer()

In [63]:
l = list(lexer.tokenize('''((!x.(x x) y)
λx.y)'''))
l

[Token(type='LPAR', value='(', lineno=1, index=0),
 Token(type='LPAR', value='(', lineno=1, index=1),
 Token(type='LAMBDA', value='!', lineno=1, index=2),
 Token(type='VAR', value='x', lineno=1, index=3),
 Token(type='POINT', value='.', lineno=1, index=4),
 Token(type='LPAR', value='(', lineno=1, index=5),
 Token(type='VAR', value='x', lineno=1, index=6),
 Token(type='VAR', value='x', lineno=1, index=8),
 Token(type='RPAR', value=')', lineno=1, index=9),
 Token(type='VAR', value='y', lineno=1, index=11),
 Token(type='RPAR', value=')', lineno=1, index=12),
 Token(type='LAMBDA', value='λ', lineno=2, index=14),
 Token(type='VAR', value='x', lineno=2, index=15),
 Token(type='POINT', value='.', lineno=2, index=16),
 Token(type='VAR', value='y', lineno=2, index=17),
 Token(type='RPAR', value=')', lineno=2, index=18)]

In [64]:
list(lexer.tokenize('!x.[y z]'))

LambdaSyntaxError: Caractère illégal : [ at position 3

## Analyseur syntaxique

Voici la grammaire du langage décrivant les $\lambda$-termes

    term ::= VAR | LAMBDA VAR POINT term | LPAR term term RPAR


In [5]:
from sly import Parser

In [6]:
class Lambda_parser(Parser):
    tokens = Lambda_lexer.tokens
    
    @_('VAR')
    def term(self, p):
        return Lambda_terme(0, p[0])
    
    @_('LAMBDA VAR POINT term')
    def term(self, p):
        return Lambda_terme(1, p[1], p.term)
    
    @_('LPAR term term RPAR')
    def term(self, p):
        return Lambda_terme(2, p.term0, p.term1)

In [7]:
parser = Lambda_parser()

## La classe `Lambda_terme`

In [8]:
def autre_variable(var, variables):
    n = 0
    while var + '{:d}'.format(n) in variables:
        n += 1
    return var + '{:d}'.format(n)

class Lambda_terme():
    def __init__(self, categorie, *args):
        if categorie not in (0, 1, 2):
            raise Exception('categorie non valide')
        if categorie == 0: 
            if len(args) != 1 or not isinstance(args[0], str):
                raise Exception('mauvaise construction pour une variable')
        elif categorie == 1:
            if len(args) != 2 or not isinstance(args[0], str) or not isinstance(args[1], Lambda_terme):
                raise Exception('mauvaise construction pour une abstraction')
        else:
            if len(args) != 2 or not isinstance(args[0], Lambda_terme) or not isinstance(args[1], Lambda_terme):
                raise Exception('mauvaise construction pour une application')
        self._content = (categorie,) + tuple(args)
        
    @staticmethod
    def cree(descr):
        return parser.parse(lexer.tokenize(descr))
    
    def est_variable(self):
        return self._content[0] == 0

    def est_abstraction(self):
        return self._content[0] == 1

    def est_application(self):
        return self._content[0] == 2

    def applique(self, terme):
        if not isinstance(terme, Lambda_terme):
            raise Exception('Application impossible')
        return Lambda_terme(2, self, terme)
    
    def abstrait(self, var):
        if not isinstance(var, str):
            raise Exception("Variable d'Abstraction invalide")
        return Lambda_terme(1, var, self)
    
    def est_redex(self):
        return self.est_application() and self._content[1].est_abstraction()
    
    def est_forme_normale(self):
        if self.est_variable():
            return True
        elif self.est_abstraction():
            return self._content[2].est_forme_normale()
        else:
            return not self._content[1].est_abstraction() and all(self._content[k].est_forme_normale() for k in (1, 2))
        
    def variables_libres(self):
        if self.est_variable():
            return {self._content[1]}
        elif self.est_application():
            var_libres = self._content[2].variables_libres()
            return var_libres.union(self._content[1].variables_libres())
        else:
            var_libres = self._content[2].variables_libres()
            var_libres.discard(self._content[1])
            return var_libres
    
    def subs(self, var, terme):
        if not isinstance(var, str):
            raise Exception('subst possible uniquement pour les variables')
        if not isinstance(terme, Lambda_terme):
            raise Exception('subst possible uniquement sur un lambda-terme')
        if self.est_variable():
            if var == self._content[1]:
                return terme
            else:
                return self
        elif self.est_application():
            return Lambda_terme(2, self._content[1].subs(var, terme), self._content[2].subs(var, terme))
        else:
            var_abstr = self._content[1]
            corps_abstr = self._content[2]
            var_libres_corps = corps_abstr.variables_libres()
            if var == var_abstr or var not in var_libres_corps:
                return self
            elif var_abstr not in terme.variables_libres():
                return Lambda_terme(1, var_abstr, corps_abstr.subs(var, terme))
            else:
                nouvelle_var = autre_variable(var_abstr, corps_abstr.variables_libres())
                return Lambda_terme(1, 
                                    nouvelle_var, 
                                    corps_abstr.subs(var_abstr, Lambda_terme(0, nouvelle_var)).subs(var, terme))
                    
                
    def _reduit(self):
        if self.est_variable():
            return self, False
        elif self.est_abstraction():
            corps_reduit, est_reduit = self._content[2]._reduit()
            return (Lambda_terme(1, self._content[1], corps_reduit) if est_reduit else self, est_reduit)
        else:
            termegauche = self._content[1]
            termedroit = self._content[2]
            if termegauche.est_abstraction():
                var_abstr = termegauche._content[1]
                corps = termegauche._content[2]
                return corps.subs(var_abstr, termedroit), True
            else:
                termegauche_reduit, est_reduit = termegauche._reduit()
                if est_reduit:
                    return Lambda_terme(2, termegauche_reduit, termedroit), est_reduit
                else:
                    termedroit_reduit, est_reduit = termedroit._reduit()
                    return (Lambda_terme(2, termegauche, termedroit_reduit) if est_reduit else self, est_reduit)
                
    def reduit(self):
        return self._reduit()
            
    def __str__(self):
        if self.est_variable():
            return self._content[1]
        elif self.est_abstraction():
            return 'λ{:s}.{:s}'.format(self._content[1], str(self._content[2]))
        else:
            return '({:s} {:s})'.format(str(self._content[1]), str(self._content[2]))

In [9]:
T1 = Lambda_terme(0, "x")
T2 = Lambda_terme(1, "x", T1)
T3 = Lambda_terme.cree('(!x.x x)')

In [10]:
print(T1)
print(T2)
print(T3)

x
λx.x
(λx.x x)


In [11]:
tuple(t.est_variable() for t in (T1, T2, T3))

(True, False, False)

In [12]:
tuple(t.est_abstraction() for t in (T1, T2, T3))

(False, True, False)

In [13]:
tuple(t.est_application() for t in (T1, T2, T3))

(False, False, True)

In [14]:
tuple(t.est_redex() for t in (T1, T2, T3))

(False, False, True)

In [15]:
tuple(t.est_forme_normale() for t in (T1, T2, T3))

(True, True, False)

In [16]:
tuple(t.variables_libres() for t in (T1, T2, T3))

({'x'}, set(), {'x'})

In [17]:
print(T1, '-->', T1.subs('y', Lambda_terme.cree('(y x)')))
print(T1, '-->', T1.subs('x', Lambda_terme.cree('(y x)')))

x --> x
x --> (y x)


In [18]:
T4 = Lambda_terme.cree('!x.y')
print(T4, '-->', T4.subs('x', Lambda_terme.cree('(y z)')))
print(T4, '-->', T4.subs('y', Lambda_terme.cree('(t z)')))
print(T4, '-->', T4.subs('y', Lambda_terme.cree('(x z)')))

λx.y --> λx.y
λx.y --> λx.(t z)
λx.y --> λx0.(x z)


In [19]:
print(T3, '-->', T3.subs('y', Lambda_terme.cree('(y x)')))
print(T3, '-->', T3.subs('x', Lambda_terme.cree('(y x)')))

(λx.x x) --> (λx.x x)
(λx.x x) --> (λx.x (y x))


In [20]:
OMEGA = Lambda_terme.cree('(!x.(x x) !x.(x x))')

In [21]:
print(OMEGA)

(λx.(x x) λx.(x x))


In [22]:
OMEGA.est_redex()

True

In [23]:
OMEGA.est_forme_normale()

False

In [24]:
OMEGA.variables_libres()

set()

In [25]:
res, est_red = OMEGA.reduit()
print(res)
print(est_red)

(λx.(x x) λx.(x x))
True


In [26]:
res, est_red = Lambda_terme.cree('(!x.(eric x) vero)').reduit()
print(res, est_red)

(eric vero) True


In [27]:
def calcul(lambda_terme, nb_etapes_max=100, verbose=False):
    etape = 0
    forme_normale_atteinte = False
    if verbose: print(lambda_terme)
    while not forme_normale_atteinte and etape < nb_etapes_max:
        etape += 1
        terme_reduit, est_reduit = lambda_terme.reduit()
        if verbose: print('{:3d}: ---> {:s}'.format(etape, str(lambda_terme), str(terme_reduit)))
        forme_normale_atteinte = not est_reduit
        lambda_terme = terme_reduit
    if forme_normale_atteinte:
        if verbose: print('Forme normale calculée : {:s}'.format(str(terme_reduit)))
        return terme_reduit
    else:
        if verbose: print('Pas de forme normale atteinte après {:d} étapes de réduction'.format(etape))
        return None

In [29]:
calcul(OMEGA, nb_etapes_max=10, verbose=True)

(λx.(x x) λx.(x x))
  1: ---> (λx.(x x) λx.(x x))
  2: ---> (λx.(x x) λx.(x x))
  3: ---> (λx.(x x) λx.(x x))
  4: ---> (λx.(x x) λx.(x x))
  5: ---> (λx.(x x) λx.(x x))
  6: ---> (λx.(x x) λx.(x x))
  7: ---> (λx.(x x) λx.(x x))
  8: ---> (λx.(x x) λx.(x x))
  9: ---> (λx.(x x) λx.(x x))
 10: ---> (λx.(x x) λx.(x x))
Pas de forme normale atteinte après 10 étapes de réduction


## Entiers, successeurs, addition, multiplication et exponentiation

In [30]:
ZERO = Lambda_terme.cree('!f.!x.x')

In [31]:
UN = Lambda_terme.cree('!f.!x.(f x)')

In [32]:
DEUX = Lambda_terme.cree('!f.!x.(f (f x))')

In [33]:
SUC = Lambda_terme.cree('!n.!f.!x.(f ((n f) x))')

In [34]:
TROIS = calcul(SUC.applique(DEUX), verbose=True)

(λn.λf.λx.(f ((n f) x)) λf.λx.(f (f x)))
  1: ---> (λn.λf.λx.(f ((n f) x)) λf.λx.(f (f x)))
  2: ---> λf.λx.(f ((λf.λx.(f (f x)) f) x))
  3: ---> λf.λx.(f (λx.(f (f x)) x))
  4: ---> λf.λx.(f (f (f x)))
Forme normale calculée : λf.λx.(f (f (f x)))


In [35]:
calcul(TROIS.applique(SUC).applique(ZERO), verbose=True)

((λf.λx.(f (f (f x))) λn.λf.λx.(f ((n f) x))) λf.λx.x)
  1: ---> ((λf.λx.(f (f (f x))) λn.λf.λx.(f ((n f) x))) λf.λx.x)
  2: ---> (λx.(λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) x))) λf.λx.x)
  3: ---> (λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) λf.λx.x)))
  4: ---> λf.λx.(f (((λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) λf.λx.x)) f) x))
  5: ---> λf.λx.(f ((λf.λx.(f (((λn.λf.λx.(f ((n f) x)) λf.λx.x) f) x)) f) x))
  6: ---> λf.λx.(f (λx.(f (((λn.λf.λx.(f ((n f) x)) λf.λx.x) f) x)) x))
  7: ---> λf.λx.(f (f (((λn.λf.λx.(f ((n f) x)) λf.λx.x) f) x)))
  8: ---> λf.λx.(f (f ((λf.λx.(f ((λf.λx.x f) x)) f) x)))
  9: ---> λf.λx.(f (f (λx.(f ((λf.λx.x f) x)) x)))
 10: ---> λf.λx.(f (f (f ((λf.λx.x f) x))))
 11: ---> λf.λx.(f (f (f (λx.x x))))
 12: ---> λf.λx.(f (f (f x)))
Forme normale calculée : λf.λx.(f (f (f x)))


In [ ]:
ADD = Lambda_terme.cree('!n.!m.!f.!x.((n f) ((m f) x))')

In [ ]:
QUATRE = calcul(ADD.applique(UN).applique(TROIS), verbose=True)

In [ ]:
CINQ = calcul(ADD.applique(TROIS).applique(DEUX), verbose=True)

In [ ]:
SEPT = calcul(ADD.applique(QUATRE).applique(TROIS), verbose=True)

In [ ]:
MUL = Lambda_terme.cree('!n.!m.!f.(n (m f))')

In [ ]:
SIX = calcul(MUL.applique(DEUX).applique(TROIS), verbose=True)

In [ ]:
EXP = Lambda_terme.cree('!n.!m.(m n)')

In [ ]:
HUIT = calcul(EXP.applique(DEUX).applique(TROIS), verbose=True)

In [ ]:
NEUF = calcul(EXP.applique(TROIS).applique(DEUX), verbose=True)

## Booléens, opérateurs logiques et conditionnelles

In [ ]:
VRAI = Lambda_terme.cree('!x.!y.x')

In [ ]:
FAUX = Lambda_terme.cree('!x.!y.y')

In [ ]:
COND = Lambda_terme.cree('!c.!a.!s.((c a) s)') 

In [ ]:
calcul(COND.applique(VRAI).applique(UN).applique(DEUX), verbose=True)

In [ ]:
calcul(COND.applique(FAUX).applique(UN).applique(DEUX), verbose=True)

In [ ]:
ET = COND.applique(Lambda_terme.cree('a')).applique(Lambda_terme.cree('b')).applique(FAUX).abstrait('b').abstrait('a')

In [ ]:
print(ET)

In [ ]:
calcul(ET.applique(VRAI).applique(VRAI), verbose=True)

In [ ]:
calcul(ET.applique(VRAI).applique(FAUX), verbose=True)

In [ ]:
calcul(ET.applique(FAUX).applique(VRAI), verbose=True)

In [ ]:
calcul(ET.applique(FAUX).applique(FAUX), verbose=True)

In [ ]:
OU = COND.applique(Lambda_terme.cree('a')).applique(VRAI).applique(Lambda_terme.cree('b')).abstrait('b').abstrait('a')

In [ ]:
calcul(OU.applique(VRAI).applique(VRAI), verbose=True)

In [ ]:
calcul(OU.applique(VRAI).applique(FAUX), verbose=True)

In [ ]:
calcul(OU.applique(FAUX).applique(VRAI), verbose=True)

In [ ]:
calcul(OU.applique(FAUX).applique(FAUX), verbose=True)

In [ ]:
NON = COND.applique(Lambda_terme.cree('a')).applique(FAUX).applique(VRAI).abstrait('a')

In [ ]:
calcul(NON.applique(VRAI), verbose=True)

In [ ]:
calcul(NON.applique(FAUX), verbose=True)

In [ ]:
NUL = Lambda_terme.cree('!n.((n !x.{:s}) {:s})'.format(str(FAUX), str(VRAI)))

In [ ]:
print(NUL)

In [ ]:
calcul(NUL.applique(ZERO), verbose=True)

In [ ]:
calcul(NUL.applique(TROIS), verbose=True)

## Couples

In [ ]:
CONS = COND.applique(Lambda_terme.cree('s')).applique(Lambda_terme.cree('x')).applique(Lambda_terme.cree('y')).abstrait('s').abstrait('y').abstrait('x')

In [ ]:
print(CONS)

In [ ]:
UN_DEUX = calcul(CONS.applique(UN).applique(DEUX), verbose=True)

In [ ]:
CAR = Lambda_terme.cree('c').applique(VRAI).abstrait('c')

In [ ]:
print(CAR)

In [ ]:
calcul(CAR.applique(UN_DEUX), verbose=True)

In [ ]:
CDR = Lambda_terme.cree('c').applique(FAUX).abstrait('c')

In [ ]:
calcul(CDR.applique(UN_DEUX), verbose=True)

In [ ]:
M_PRED = Lambda_terme.cree('!n.(CAR ((n !c.((CONS (CDR c)) (SUC (CDR c)))) ((CONS ZERO) ZERO)))')
print(M_PRED)
PRED = M_PRED.subs('CAR', CAR).subs('CONS', CONS).subs('CDR', CDR).subs('SUC', SUC).subs('ZERO', ZERO)
print(PRED)

In [ ]:
calcul(PRED.applique(DEUX), verbose=True)

In [ ]:
calcul(PRED.applique(ZERO), verbose=True)

In [ ]:
M_SUB = Lambda_terme.cree('!n.!m.((m PRED) n)')
print(M_SUB)
SUB = M_SUB.subs('PRED', PRED)
print(SUB)

In [ ]:
calcul(SUB.applique(TROIS).applique(UN), verbose=True)

In [ ]:
M_INF = Lambda_terme.cree('!n.!m.(NUL ((SUB m) n))')
print(M_INF)
INF = M_INF.subs('NUL', NUL).subs('SUB', SUB)
#lambda n: lambda m: est_nul(sub(m)(n))

In [ ]:
calcul(INF.applique(TROIS).applique(UN), verbose=True)

In [ ]:
calcul(INF.applique(UN).applique(TROIS), verbose=True)

In [ ]:
calcul(INF.applique(UN).applique(UN), verbose=True)

In [ ]:
M_EGAL = Lambda_terme.cree('!n.!m.((ET ((INF n) m)) ((INF m) n))')
print(M_EGAL)
EGAL = M_EGAL.subs('ET', ET).subs('INF', INF)
print(EGAL)

In [ ]:
print(calcul(EGAL.applique(UN).applique(UN)))

In [ ]:
print(calcul(EGAL.applique(UN).applique(DEUX)))

## Itération

In [ ]:
M_FACTv1 = Lambda_terme.cree('!n.(CDR ((n !c.((CONS (SUC (CAR c))) ((MUL (SUC (CAR c))) (CDR c)))) ((CONS ZERO) UN)))')
print(M_FACTv1)
FACTv1 = M_FACTv1.subs('CONS', CONS).subs('CAR', CAR).subs('CDR', CDR).subs('SUC', SUC).subs('MUL', MUL).subs('UN', UN).subs('ZERO', ZERO)
print(FACTv1)

In [ ]:
print(calcul(FACTv1.applique(ZERO)))

In [ ]:
print(calcul(FACTv1.applique(UN)))

In [ ]:
print(calcul(FACTv1.applique(DEUX)))

In [ ]:
print(calcul(FACTv1.applique(DEUX), nb_etapes_max=200))

In [ ]:
print(calcul(FACTv1.applique(TROIS), nb_etapes_max=500))

In [ ]:
print(calcul(FACTv1.applique(QUATRE), nb_etapes_max=1700))

## Et la récursivité ? 

In [ ]:
M_PHI_FACT = Lambda_terme.cree('!f.!n.(((COND ((EGAL n) ZERO)) UN) ((MUL n) (f (PRED n))))')
print(M_PHI_FACT)
PHI_FACT = M_PHI_FACT.subs('COND', COND).subs('EGAL', EGAL).subs('ZERO', ZERO).subs('UN', UN).subs('MUL', MUL).subs('PRED', PRED)

In [ ]:
BOTTOM = Lambda_terme.cree('!y.OMEGA').subs('OMEGA', OMEGA)
print(BOTTOM)

In [ ]:
FACT0 = PHI_FACT.applique(BOTTOM)

In [ ]:
print(calcul(FACT0.applique(ZERO)))

In [ ]:
calcul(FACT0.applique(UN), verbose=True)

In [ ]:
FACT1 = PHI_FACT.applique(FACT0)

In [ ]:
print(calcul(FACT1.applique(ZERO)))

In [ ]:
print(calcul(FACT1.applique(UN), nb_etapes_max=200))

In [ ]:
FIX_CURRY = Lambda_terme.cree('!f.(!x.(f (x x)) !x.(f (x x)))')
print(FIX_CURRY)

In [ ]:
FACTv2 = FIX_CURRY.applique(PHI_FACT)

In [ ]:
print(calcul(FACTv2.applique(ZERO)))

In [ ]:
print(calcul(FACTv2.applique(UN), nb_etapes_max=200))

In [ ]:
print(calcul(FACTv2.applique(DEUX), nb_etapes_max=700))

In [ ]:
print(calcul(FACTv2.applique(TROIS), nb_etapes_max=4000))

In [ ]:
print(calcul(FACTv2.applique(QUATRE), nb_etapes_max=25000))

In [ ]:
PF = FIX_CURRY.applique(Lambda_terme.cree('M'))

In [ ]:
calcul(PF, verbose=True, nb_etapes_max=10)

# $\lambda$-calcul avec les lambda-expressions de Python

## Les entiers de Church

In [ ]:
zero = lambda f: lambda x: x

In [ ]:
un = lambda f: lambda x: f(x)

In [ ]:
deux = lambda f: lambda x: f(f(x))

In [ ]:
trois = lambda f: lambda x: f(f(f(x)))

In [ ]:
def entier_church_en_int(ec):
    return ec(lambda n: n+1)(0)

In [ ]:
tuple(entier_church_en_int(n) for n in (zero, un, deux, trois))

In [ ]:
suc = lambda n: lambda f: lambda x: f(n(f)(x))

In [ ]:
tuple(entier_church_en_int(suc(n)) for n in (zero, un, deux, trois)) 

In [ ]:
def int_en_entier_church(n):
    if n == 0:
        return zero
    else:
        return suc(int_en_entier_church(n - 1))

In [ ]:
tuple(entier_church_en_int(int_en_entier_church(n)) for n in range(10))

In [ ]:
add = lambda n: lambda m: lambda f: lambda x: n(f)(m(f)(x))

In [ ]:
cinq = add(deux)(trois)
entier_church_en_int(cinq)

In [ ]:
mul = lambda n: lambda m: lambda f: n(m(f))

In [ ]:
six = mul(deux)(trois)
entier_church_en_int(six)

In [ ]:
exp = lambda n: lambda m: m(n)

In [ ]:
huit = exp(deux)(trois)
entier_church_en_int(huit)

## Les booléens

In [ ]:
vrai = lambda x: lambda y: x
faux = lambda x: lambda y: y

In [ ]:
def booleen_en_bool(b):
    return b(True)(False)
    

In [ ]:
tuple(booleen_en_bool(b) for b in (vrai, faux))

In [ ]:
cond = lambda c: lambda a: lambda s: c(a)(s) 

In [ ]:
cond(vrai)(1)(2)

In [ ]:
cond(faux)(1)(2)

In [ ]:
cond(vrai)(1)(1/0)

In [ ]:
non = lambda b: cond(b)(faux)(vrai)

In [ ]:
tuple(booleen_en_bool(non(b)) for b in (vrai, faux))

In [ ]:
et = lambda b1: lambda b2: cond(b1)(b2)(faux)

In [ ]:
tuple(booleen_en_bool(et(b1)(b2)) for b1 in (vrai, faux) for b2 in (vrai, faux))

In [ ]:
ou = lambda b1: lambda b2: cond(b1)(vrai)(b2)

In [ ]:
tuple(booleen_en_bool(ou(b1)(b2)) for b1 in (vrai, faux) for b2 in (vrai, faux))

In [ ]:
est_nul = lambda n : n(lambda x: faux)(vrai)

In [ ]:
tuple(booleen_en_bool(est_nul(n)) for n in (zero, un, deux, trois, cinq, six, huit))

## Les couples

In [ ]:
cons = lambda x: lambda y: lambda z: z(x)(y)

In [ ]:
un_deux = cons(un)(deux)

In [ ]:
car = lambda c: c(vrai)
cdr = lambda c: c(faux)

In [ ]:
entier_church_en_int(car(un_deux)), entier_church_en_int(cdr(un_deux))

In [ ]:
pred = lambda n: car(n(lambda c: cons(cdr(c))(suc(cdr(c))))(cons(zero)(zero)))

In [ ]:
tuple(entier_church_en_int(pred(int_en_entier_church(n))) for n in range(10))

In [ ]:
sub = lambda n: lambda m: m(pred)(n)

In [ ]:
entier_church_en_int(sub(huit)(trois))

In [ ]:
est_inf_ou_egal = lambda n: lambda m: est_nul(sub(m)(n))

In [ ]:
tuple(booleen_en_bool(est_inf_ou_egal(cinq)(int_en_entier_church(n))) for n in range(10))

In [ ]:
est_egal = lambda n: lambda m: et(est_inf_ou_egal(n)(m))(est_inf_ou_egal(m)(n))

In [ ]:
tuple(booleen_en_bool(est_egal(cinq)(int_en_entier_church(n))) for n in range(10))

## Itération

In [ ]:
fact = lambda n: cdr(n(lambda c: (cons(suc(car(c)))(mul(suc(car(c)))(cdr(c)))))(cons(zero)(un)))

In [ ]:
tuple(entier_church_en_int(fact(int_en_entier_church(n))) for n in range(7))

## Combinateur de point fixe

In [ ]:
phi_fact = lambda f: lambda n: 1 if n == 0 else n*f(n-1)

In [ ]:
bottom = lambda x: (lambda y: y(y))(lambda y:y(y))

In [ ]:
f0 = phi_fact(bottom)
f1 = phi_fact(f0)
f2 = phi_fact(f1)
f3 = phi_fact(f2)
f4 = phi_fact(f3)

In [ ]:
tuple(f4(n) for n in range(4))

In [ ]:
def fact_rec(n):
    if n == 0:
        return 1
    else:
        return n * fact_rec(n - 1)

In [ ]:
fact2 = phi_fact(fact_rec)

In [ ]:
tuple(fact2(n) for n in range(7))

In [ ]:
fix_curry = lambda f: (lambda x: lambda y: f(x(x))(y))(lambda x: lambda y: f(x(x))(y))

In [ ]:
fact3 = fix_curry(phi_fact)

In [ ]:
tuple(fact3(n) for n in range(7))

## Un programme obscur

In [ ]:
print((lambda x: (lambda y: lambda z: x(y(y))(z))(lambda y: lambda z: x(y(y))(z))) 
      (lambda x: lambda y: '' if y == [] else chr(y[0])+x(y[1:]))
      (((lambda x: (lambda y: lambda z: x(y(y))(z)) (lambda y: lambda z: x(y(y))(z)))
        (lambda x: lambda y: lambda z: [] if z == [] else [y(z[0])]+x(y)(z[1:])))      
       (lambda x: (lambda x: (lambda y: lambda z: x(y(y))(z))(lambda y: lambda z: x(y(y))(z)))
        (lambda x: lambda y: lambda z: lambda t: 1 if t == 0 else (lambda x: ((lambda u: 1 if u == 0 else z)(t % 2)) * x * x % y)
         (x(y)(z)(t // 2)))(989)(x)(761))
       ([377, 900, 27, 27, 182, 647, 163, 182, 390, 27, 726, 937])))

In [ ]:
phiListEnChaine = lambda x: lambda y: '' if y == [] else chr(y[0]) + x(y[1:])

In [ ]:
fix_curry(phiListEnChaine)([65+k for k in range(26)])

In [ ]:
phiMap = lambda x: lambda y: lambda z: [] if z == [] else [y(z[0])] + x(y)(z[1:])

In [ ]:
fix_curry(phiMap)(lambda x: x*x)([1, 2, 3, 4])

In [ ]:
phiExpoMod = lambda x: lambda y: lambda z: lambda t: 1 if z == 0 else (lambda u: 1 if u == 0 else y)(z % 2) * x(y)(z//2)(t) ** 2 % t

In [ ]:
fix_curry(phiExpoMod)(2)(10)(1000)